# Atividade prática: Mineração de Dados - Semana 04

Notebook criado para acompanhar as atividades práticas da Semana 04, apresentadas pela disciplina de **Mineração de Dados** da **UNIVESP**.

## Objetivos da Semana 04:

Usar árvores de decisão para classificar um conjunto de dados sobre aceitabilidade de carros de acordo com as suas características.

## Exercícios:

1. Separar dados entre treinamento e teste, e medir a acurácia do classificador. Para o treino, separe 20% dos dados.

2. Gerar a imagem da árvore de decisão obtida no treinamento.


### Base de Dados:
https://archive.ics.uci.edu/ml/datasets/Car+Evaluation

### Sobre o dataframe:

Contém informações sobre as características de um conjunto de carros.

O **dicionário de dados** da base é o seguinte:

* **buying (v-high, high, med, low):** preço de compra (muito alto, alto, médio, baixo);
* **maint (v-high, high, med, low):** preço de manutenção (muito alto, alto, médio, baixo);
* **doors (2,3,4,5-more):** número de portas (2,3,4,5-mais);
* **persons (2, 4, more):** capacidade de pessoas no carro (2, 4, mais);
* **lug_boot (small, med, big):** tamanho do bagageiro (pequeno, médio, grande);
* **safety (low, med, high):** segurança estimada do carro (baixa, média, alta);
* **acc (unacc, acc, good, v-good):** aceitabilidade (inaceitável, aceitável, bom, muito bom).

In [11]:
import pandas as pd
import matplotlib.pyplot as plt

## Biblioteca e módulos necessários para plotar a árvore de decisão:
from sklearn import tree
from sklearn.tree import DecisionTreeClassifier, plot_tree

## Biblioteca e módulos necessários para o treinamento e teste do conjunto de dados:
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

In [12]:
url = 'https://raw.githubusercontent.com/nagelamartins/Mineracao_de_dados/refs/heads/main/Base-dados_Sem-04.csv'
df = pd.read_csv(url)
df.head()

buying  maint doors persons lug_boot safety    acc
0  vhigh  vhigh     2       2    small    low  unacc
1  vhigh  vhigh     2       2    small    med  unacc
2  vhigh  vhigh     2       2    small   high  unacc
3  vhigh  vhigh     2       2      med    low  unacc
4  vhigh  vhigh     2       2      med    med  unacc

Para facilitar a leitura do dataframe, as colunas são renomeadas de acordo com os atributos que as representam:

In [13]:
renomear_colunas = {
    'buying': 'compra',
    'maint': 'manutencao',
    'doors': 'portas',
    'persons': 'pessoas',
    'lug_boot': 'bagageiro',
    'safety': 'seguranca',
    'acc': 'aceitabilidade'
}

df = df.rename(columns=renomear_colunas)
df.columns

Index(['compra', 'manutencao', 'portas', 'pessoas', 'bagageiro', 'seguranca',
       'aceitabilidade'],
      dtype='object')

Verificando as informações da tabela, nota-se que não existem campos nulos, porém, todos eles possuem o tipo "object":

In [14]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1728 entries, 0 to 1727
Data columns (total 7 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   compra          1728 non-null   object
 1   manutencao      1728 non-null   object
 2   portas          1728 non-null   object
 3   pessoas         1728 non-null   object
 4   bagageiro       1728 non-null   object
 5   seguranca       1728 non-null   object
 6   aceitabilidade  1728 non-null   object
dtypes: object(7)
memory usage: 94.6+ KB


Os dados são então mapeados para tipos numéricos que possibilitam a utilização dos algoritmos de classificação:

In [15]:
df['compra'] = df['compra'].map({'vhigh': 3, 'high': 2, 'med': 1, 'low': 0})
df['manutencao'] = df['manutencao'].map({'vhigh': 3, 'high': 2, 'med': 1, 'low': 0})
df['portas'] = df['portas'].map({'2': 2,'3': 3,'4': 4,'5more': 5})
df['pessoas'] = df['pessoas'].map({'2': 2,'4': 4,'more': 5})
df['bagageiro'] = df['bagageiro'].map({'small': 0, 'med': 1, 'big': 2})
df['seguranca'] = df['seguranca'].map({'low': 0, 'med': 1, 'high': 2})
df['aceitabilidade'] = df['aceitabilidade'].map({'unacc': 0, 'acc': 1, 'good': 2, 'vgood': 3})

df.head()

compra  manutencao  portas  pessoas  bagageiro  seguranca  aceitabilidade
0       3           3       2        2          0          0               0
1       3           3       2        2          0          1               0
2       3           3       2        2          0          2               0
3       3           3       2        2          1          0               0
4       3           3       2        2          1          1               0

Os dados são, agora, separados em duas partes: as características (armazenadas na variável `atributos`) que o modelo utilizará para aprender, e a variável-alvo, que o modelo tentará prever (variável `classes`).

*Obs: a lista de atributos gerada na variável `atributo_nomes` auxilia na legibilidade e manutenção do código, portanto, foi utilizada como uma boa prática. Apesar disso, esses atributos poderiam ter sido passados diretamente na variável `atributos`.*

In [16]:
atributos_nomes = df.columns[0:5]
atributos = df[atributos_nomes]
classes = df['aceitabilidade']


Com as variáveis `atributos` e `classes` definidas, os dados podem ser separados entre treinamento e teste com a função `train_test_split` da biblioteca `scikit-learn`.
* O parâmetro `test_size=0.2` especifica que 20% dos dados serão usados para o conjunto de teste, e os restantes 80% para o treinamento;
* `stratify=classes` garante que a proporção de cada classe (inaceitável, aceitável, bom, muito bom) seja a mesma nos conjuntos de treinamento e teste. (Importante para conjuntos de dados desbalanceados, onde algumas classes têm muito mais exemplos do que outras);
* E `random_state=10` define um valor inicial para o gerador de números aleatórios. Usar um random_state garante que a divisão dos dados seja a mesma toda vez que você executar o código (Útil para reprodutibilidade).

In [17]:
atributos_treino, atributos_teste, classes_treino, classes_teste = train_test_split(atributos, classes, test_size=0.2, stratify=classes, random_state=10)

Usando os dados de treinamento, a árvore de decisão é construída, utilizando a função `DecisionTreeClassifier` da biblioteca `scikit-learn`.  
* A linha `arvore = DecisionTreeClassifier()` instancia uma árvore de decisão vazia utilizando os parâmetros padrão da função;
* Com a árvore instanciada, o método `.fit()` é usado para treiná-la. É ele quem recebe os dados de treinamento (`atributos_treino`, `classes_treino`).

*Durante o treinamento, o algoritmo da árvore de decisão analisa esses dados para encontrar os melhores pontos de divisão nas características que ajudam a separar as classes. Ele constrói a estrutura da árvore (nós de decisão e folhas) com base nesses padrões encontrados nos dados de treinamento.*



In [18]:
arvore = DecisionTreeClassifier()
arvore = arvore.fit(atributos_treino,classes_treino)

Agora é verificada a acurácia da árvore de decisão treinada.
* A linha `classes_predicao = arvore.predict(atributos_teste)`usa o modelo da árvore de decisão treinado (`arvore`) para fazer previsões sobre os dados de teste (`atributos_teste`). O método `.predict()` recebe as características dos carros de teste e retorna uma lista das classes previstas (`classes_predicao`) para cada carro;
* `acuracia = accuracy_score(classes_teste, classes_predicao)`: Esta linha calcula a acurácia do classificador. `accuracy_score` é uma métrica que compara os rótulos reais do conjunto de teste (`classes_teste`) com os rótulos previstos pelo seu modelo (`classes_predicao)`.  
* `print('Acurácia do classificador: {}'.format(acuracia))`: Esta linha imprime a acurácia calculada no console.  

*A acurácia é a proporção de previsões corretas feitas pelo modelo. Um valor de 1.0 significa que o modelo previu todas as classes corretamente no conjunto de teste.   
No modelo, a acurácia é de aproximadamente 0,607, o que significa que ele previu corretamente a classe de aceitabilidade para cerca de 60.7% dos carros no conjunto de teste.*

In [21]:
classes_predicao = arvore.predict(atributos_teste)
acuracia = accuracy_score(classes_teste, classes_predicao)
print('Acurácia do classificador: {}'.format(acuracia))

Acurácia do classificador: 0.6069364161849711


Por fim, é gerada a visualização da árvore de decisão treinada.
* A linha `plt.figure(figsize=(200,120))` define o tamanho da visualização. São passados valores grandes para facilitar a visualização da árvore, devido a sua complexidade;  
* `plot_tree(arvore, filled=True, rounded=True, class_names=['Inaceitavel', 'Aceitavel', 'Bom', 'Muito bom'], feature_names=atributos_nomes)`: Função que gera a visualização da árvore, de acordo com os parâmetros informados:
    - `arvore`: O objeto da árvore de decisão a ser visualizado;
    - `filled=True`: Preenche os nós da árvore com cores para indicar a classe majoritária naquele nó;
    - `rounded=True`: Arredonda as caixas dos nós para uma aparência mais agradável;
    - `class_names=['Inaceitavel', 'Aceitavel', 'Bom', 'Muito bom']`: Fornece os nomes das classes de destino. Isso faz com que os rótulos nas folhas da árvore sejam mais informativos do que apenas números (0, 1, 2, 3);
     - `feature_names=atributos_nomes`: Fornece os nomes dos atributos. Isso faz com que os critérios de divisão em cada nó da árvore sejam mais fáceis de entender.
* `plt.show()`: exibe a figura que foi criada.  

*Como a imagem gerada é muito grande, pode ser necessário salvá-la para visualizá-la em detalhes.*

In [24]:
plt.figure(figsize=(200,120))
plot_tree(arvore, filled=True, rounded=True, class_names=['Inaceitavel', 'Aceitavel', 'Bom', 'Muito bom'], feature_names=atributos_nomes)
plt.show()